In [171]:
%pip install matplotlib


[notice] A new release of pip is available: 24.3.1 -> 26.0.1
[notice] To update, run: python3 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [172]:
%pip install tqdm


[notice] A new release of pip is available: 24.3.1 -> 26.0.1
[notice] To update, run: python3 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [173]:
%pip install tensorflow


[notice] A new release of pip is available: 24.3.1 -> 26.0.1
[notice] To update, run: python3 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [174]:
%pip install tqdm


[notice] A new release of pip is available: 24.3.1 -> 26.0.1
[notice] To update, run: python3 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [237]:
import matplotlib.pyplot as plt
import numpy as np
import string
import os
import time
from pickle import dump, load
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.applications.xception import Xception, preprocess_input
from tensorflow.keras.preprocessing.image import img_to_array, load_img
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical, get_file
from tensorflow.keras.layers import Add 
from tensorflow.keras.models import Model, load_model
from tensorflow.keras.layers import Input, Dense, LSTM, Embedding, Dropout
from tqdm.notebook import tqdm as tqdm
from PIL import Image
# tqdm().pandas()


### Load any type of document. Whether it is an image or a text file

In [176]:
def load_doc(filename):
    file = open(filename, 'r')
    text = file.read()
    file.close()
    return text

In [177]:
def all_img_captions(filename):
    file = load_doc(filename)
    captions = file.split('\n')
    descriptions = {}
    for caption in captions[:-1]:
        image, caption = caption.split('\t')
        if image[:-2] not in descriptions:
            descriptions[image[:-2]] = [caption]
        else:
            descriptions[image[:-2]].append(caption)
    return descriptions

In [178]:
def clean_text(captions):
    table = str.maketrans('','',string.punctuation)
    for image, caps in captions.items():
        for i, image_caption in enumerate(caps):
            image_caption.replace("-","")
            desc = image_caption.split()
            desc = [word.lower() for word in desc]
            desc = [word.translate(table) for word in desc]
            desc = [word for word in desc if len(word) > 1]
            desc = [word for word in desc if word.isalpha()]

            image_caption = ' '.join(desc)
            captions[image][i] = image_caption
    return captions

In [179]:
def text_vocabulary(descriptions):
    vocab = set()
    for key in descriptions:
        [vocab.update(d.split()) for d in descriptions[key]]
    return vocab

In [180]:
def save_descriptions(descriptions,filename):
    lines = list()
    for key, desc_list in descriptions.items():
        for desc in desc_list:
            lines.append(key+'\t'+desc)
    data = '\n'.join(lines)
    file = open(filename,'w')
    file.write(data)
    file.close

In [181]:
dataset_text_dir_name = "Flickr8k_text"
dataset_images_dir_name = "Flicker8k_Dataset"

In [182]:
token_filename = dataset_text_dir_name + '/Flickr8k.token.txt'
descriptions = all_img_captions(token_filename)
print("Length of descriptions: ", len(descriptions))

Length of descriptions:  8092


In [183]:
cleaned_description = clean_text(descriptions)
vocabulary = text_vocabulary(cleaned_description)
print("Length of Vocab: ", len(vocabulary))

Length of Vocab:  8763


In [184]:
save_descriptions(cleaned_description,"descriptions.txt")

In [185]:
def download_with_retry(url, filename, max_retries = 3):
    for attempt in range(max_retries):
        try:
            return get_file(filename, url)
        except Exception as e:
            if attempt == max_retries - 1 :
                raise e
            print("Download attempt failed")
            time.sleep(3)

In [186]:
weights_url = "file:///Users/abhiramdeshpande/Desktop/development/ML Projects/Image Caption Generator/xception_weights.h5"
weights_path = download_with_retry(weights_url, "xception_weights.h5")
print(weights_path)

/Users/abhiramdeshpande/.keras/datasets/xception_weights.h5


In [233]:
%pip install tensorflow-macos

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.1/227.1 MB 854.8 kB/s eta 0:00:0000:0100:07
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.7/13.7 MB 372.0 kB/s eta 0:00:0000:0100:02
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.5/5.5 MB 545.6 kB/s eta 0:00:00a 0:00:01
  Attempting uninstall: protobuf
    Found existing installation: protobuf 6.33.5
    Uninstalling protobuf-6.33.5:
      Successfully uninstalled protobuf-6.33.5
  Attempting uninstall: numpy
    Found existing installation: numpy 2.4.2
    Uninstalling numpy-2.4.2:
      Successfully uninstalled numpy-2.4.2
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
  NOTE: The current PATH contains path(s) starting with `~`, which may not be expanded by all applications.
  Attempting uninstall: tensorboard
    Found existing installation: tensorboard 2.20.0
    Uninstalling tensorboard-2.20.0:
      Successfully uninstalled tensorboard-2.20.0
  Consider adding this

In [234]:
%pip install tensorflow-metal

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.4/1.4 MB 904.2 kB/s eta 0:00:000:00:01

[notice] A new release of pip is available: 24.3.1 -> 26.0.1
[notice] To update, run: python3 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [239]:
import tensorflow as tf

gpus = tf.config.list_physical_devices('GPU')
if gpus:
    print("Available GPUs:")
    for gpu in gpus:
        print(gpu)
else:
    print("No GPUs found or TensorFlow is not configured correctly to use them.")


No GPUs found or TensorFlow is not configured correctly to use them.


In [231]:
def extract_features(directory):
    model = Xception(include_top = False, pooling = 'avg', weights = weights_path)
    features = {}
    valid_images_extension = ['.jpg','.jpeg','.png']
    for img in os.listdir(directory):
        extension = os.path.splitext(img)[1].lower()
        if extension not in valid_images_extension:
            continue
        filename = directory + '/' + img
        image = Image.open(filename)
        image = image.resize((299,299))
        image = np.expand_dims(image, axis= 0)
        image = image/127.5
        image = image - 1.0

        feature = model.predict(image)
        print(feature)
        features[img] = feature
    print("Extracted features: ",features)
    return features


In [207]:
features = extract_features(dataset_images_dir_name)
dump(features, open("features.p","wb"))

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 476ms/step
[[0.2548105  0.         0.21400751 ... 0.22789013 0.00312031 0.7336313 ]]
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 63ms/step
[[0.19488221 0.11717104 0.01153503 ... 0.08871817 0.21722704 0.01624626]]
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 65ms/step
[[0.4702801  0.18794514 0.00056573 ... 0.00291162 0.23279649 0.09733206]]
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 76ms/step
[[0.0012469  0.         0.10082759 ... 0.1049165  0.08133963 0.6485718 ]]
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
[[0.15289305 0.06944707 0.1274265  ... 0.         0.0584477  0.23223752]]
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 66ms/step
[[0.0880283  0.04602135 0.04978133 ... 0.         0.         0.3709157 ]]
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
[[0.00868513 0.04271312 0.06814158 ... 0.         0.         0.1472107 ]]
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 76ms/step
[[0.09389455 0.08985976 0.30394787 ... 0.07283571 0.         0.0071027 ]]
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 67ms/step
[[2.0046560e-02 3.3327875e-01 3.5326949e-01 ... 8.8805579e-02
  1

In [208]:
features

{'2387197355_237f6f41ee.jpg': array([[0.2548105 , 0.        , 0.21400751, ..., 0.22789013, 0.00312031,
         0.7336313 ]], shape=(1, 2048), dtype=float32),
 '2609847254_0ec40c1cce.jpg': array([[0.19488221, 0.11717104, 0.01153503, ..., 0.08871817, 0.21722704,
         0.01624626]], shape=(1, 2048), dtype=float32),
 '2046222127_a6f300e202.jpg': array([[0.4702801 , 0.18794514, 0.00056573, ..., 0.00291162, 0.23279649,
         0.09733206]], shape=(1, 2048), dtype=float32),
 '2853743795_e90ebc669d.jpg': array([[0.0012469 , 0.        , 0.10082759, ..., 0.1049165 , 0.08133963,
         0.6485718 ]], shape=(1, 2048), dtype=float32),
 '2696951725_e0ae54f6da.jpg': array([[0.15289305, 0.06944707, 0.1274265 , ..., 0.        , 0.0584477 ,
         0.23223752]], shape=(1, 2048), dtype=float32),
 '3421131122_2e4bde661e.jpg': array([[0.0880283 , 0.04602135, 0.04978133, ..., 0.        , 0.        ,
         0.3709157 ]], shape=(1, 2048), dtype=float32),
 '3229730008_63f8ca2de2.jpg': array([[0.008685

In [209]:
def load_photos(filename):
    file = load_doc(filename)
    photos = file.split('\n')[:-1]
    photos_present = [photo for photo in photos if os.path.exists(os.path.join(dataset_images_dir_name, photo))]
    return photos_present

In [210]:
def load_clean_descriptions(filename, photos):
    file = load_doc(filename)
    descriptions = {}
    for line in file.split('\n'):
        words = line.split()
        if len(words) < 1:
            continue
        image,image_caption = words[0], words[1:]
        if image in photos:
            descriptions[image] = []
            desc = '<start> '+" ".join(image_caption) + ' <end>'
            descriptions[image].append(desc)
    return descriptions

In [211]:
def load_features(train_images):
    all_features = load(open("features.p", 'rb'))
    print("All Features: ", all_features)
    features = {k: all_features[k] for k in train_images}
    return features

In [212]:
token_filename = dataset_text_dir_name + '/Flickr_8k.trainImages.txt'

# train_images is a list of all the training images that are present in the dataset
train_images = load_photos(token_filename)

print("train_images: ", train_images[:5])
print("Length of training photos: ", len(train_images))

train_descriptions = load_clean_descriptions("descriptions.txt", train_images)
print("Length of training descriptions: ", len(train_descriptions))
train_features = load_features(train_images)
# print("Length of training features: ", len(train_features))

train_images:  ['2513260012_03d33305cf.jpg', '2903617548_d3e38d7f88.jpg', '3338291921_fe7ae0c8f8.jpg', '488416045_1c6d903fe0.jpg', '2644326817_8f45080b87.jpg']
Length of training photos:  6000
Length of training descriptions:  6000
All Features:  {'2387197355_237f6f41ee.jpg': array([[0.2548105 , 0.        , 0.21400751, ..., 0.22789013, 0.00312031,
        0.7336313 ]], shape=(1, 2048), dtype=float32), '2609847254_0ec40c1cce.jpg': array([[0.19488221, 0.11717104, 0.01153503, ..., 0.08871817, 0.21722704,
        0.01624626]], shape=(1, 2048), dtype=float32), '2046222127_a6f300e202.jpg': array([[0.4702801 , 0.18794514, 0.00056573, ..., 0.00291162, 0.23279649,
        0.09733206]], shape=(1, 2048), dtype=float32), '2853743795_e90ebc669d.jpg': array([[0.0012469 , 0.        , 0.10082759, ..., 0.1049165 , 0.08133963,
        0.6485718 ]], shape=(1, 2048), dtype=float32), '2696951725_e0ae54f6da.jpg': array([[0.15289305, 0.06944707, 0.1274265 , ..., 0.        , 0.0584477 ,
        0.23223752]], 

In [213]:
def dic_to_list(descriptions):
    all_desc = []
    for key in descriptions.keys():
        [all_desc.append(d) for d in descriptions[key]]
    return all_desc

In [214]:
def create_tokenizer(descriptions):
    desc_list = dic_to_list(descriptions)
    tokenizer = Tokenizer()
    tokenizer.fit_on_texts(desc_list)
    return tokenizer

In [215]:
tokenizer  = create_tokenizer(train_descriptions)

In [216]:
dump(tokenizer, open("tokenizer.p","wb"))

In [217]:
vocab_size = len(tokenizer.word_index) + 1
print("Vocabulary Size: ", vocab_size)

Vocabulary Size:  3836


In [218]:
def max_length_descriptions(descriptions):
    desc_list = dic_to_list(descriptions)
    return max(len(d.split()) for d in desc_list)

In [219]:
max_length = max_length_descriptions(train_descriptions)
print("Max Length of descriptions: ", max_length)

Max Length of descriptions:  34


In [220]:
def data_generator(descriptions, features, tokenizer, max_length, vocab_size):
    def generator():
        while True:
            for key, description_list in descriptions.items():
                feature = features[key][0]
                input_img, input_seq, output_word = create_sequences(tokenizer, max_length, description_list, feature, vocab_size)
                for i in range(len(input_img)):
                    yield {'input_1': input_img[i], 'input_2': input_seq[i]}, output_word[i] 
    output_signature = (
            {
                'input_1': tf.TensorSpec(shape=(2048,), dtype=tf.float32), 
                'input_2': tf.TensorSpec(shape=(max_length,), dtype=tf.int32)
            },
            tf.TensorSpec(shape=(vocab_size,), dtype=tf.float32)  
        )    
    dataset = tf.data.Dataset.from_generator(generator, output_signature=output_signature)
    return dataset.batch(64)

In [ ]:
def create_sequences(tokenizer, max_length, description_list, feature, vocab_size):
    input_img, input_seq, output_word = [], [], []
    for description in description_list:
        seq = tokenizer.texts_to_sequences([description])[0]
        for i in range(1, len(seq)):
            in_seq, out_seq = seq[:i], seq[i]
            in_seq = pad_sequences([in_seq], maxlen=max_length)[0]
            out_seq = to_categorical([out_seq], num_classes=vocab_size)[0]
            input_img.append(feature)
            input_seq.append(in_seq)
            output_word.append(out_seq)
    return np.array(input_img), np.array(input_seq), np.array(output_word)

In [222]:
dataset = data_generator(train_descriptions, train_features, tokenizer, max_length, vocab_size)
# dataset = dataset.prefetch(buffer_size=tf.data.AUTOTUNE)
for (a,b) in dataset.take(1):
    print(a['input_1'].shape)
    print(a['input_2'].shape)
    print(b.shape)

(64, 2048)
(64, 34)
(64, 3836)


2026-02-19 23:12:08.183783: I tensorflow/core/framework/local_rendezvous.cc:407] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


In [223]:
def define_model(vocab_size, max_length):

    #CNN model from which we will extract the features from the image
    # from 2048 nodes to 256 nodes
    inputs1 = Input(shape=(2048,))
    fe1 = Dropout(0.5)(inputs1)
    fe2 = Dense(256, activation='relu')(fe1)

    #LSTM model which will take the caption as input and output a vector of 256 nodes
    inputs2 = Input(shape=(max_length,))
    se1 = Embedding(vocab_size, 256, mask_zero=True)(inputs2)
    se2 = Dropout(0.5)(se1)
    se3 = LSTM(256)(se2)

    # Decoder model which will take the output from both the CNN and LSTM and output
    # a probability distribution over the vocabulary

    decoder1 = Add()([fe2, se3])
    decoder2 = Dense(256, activation='relu')(decoder1)
    outputs = Dense(vocab_size, activation='softmax')(decoder2)

    model = Model(inputs=[inputs1, inputs2], outputs=outputs)
    model.compile(loss='categorical_crossentropy', optimizer='adam')
    return model


In [224]:
model.summary()

Model: "xception"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_9       │ (None, None,      │          0 │ -                 │
│ (InputLayer)        │ None, 3)          │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1_conv1        │ (None, None,      │        864 │ input_layer_9[0]… │
│ (Conv2D)            │ None, 32)         │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1_conv1_bn     │ (None, None,      │        128 │ block1_conv1[0][… │
│ (BatchNormalizatio… │ None, 32)         │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1_conv1_act    │ (None, None,      │          0 │ block1_conv1_bn[… │
│ (Activation)        │ None, 32)         │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1_conv2        │ (None, None,      │     18,432 │ block1_conv1_act… │
│ (Conv2D)            │ None, 64)         │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1_conv2_bn     │ (None, None,      │        256 │ block1_conv2[0][… │
│ (BatchNormalizatio… │ None, 64)         │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block1_conv2_act    │ (None, None,      │          0 │ block1_conv2_bn[… │
│ (Activation)        │ None, 64)         │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block2_sepconv1     │ (None, None,      │      8,768 │ block1_conv2_act… │
│ (SeparableConv2D)   │ None, 128)        │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block2_sepconv1_bn  │ (None, None,      │        512 │ block2_sepconv1[… │
│ (BatchNormalizatio… │ None, 128)        │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block2_sepconv2_act │ (None, None,      │          0 │ block2_sepconv1_… │
│ (Activation)        │ None, 128)        │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block2_sepconv2     │ (None, None,      │     17,536 │ block2_sepconv2_… │
│ (SeparableConv2D)   │ None, 128)        │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block2_sepconv2_bn  │ (None, None,      │        512 │ block2_sepconv2[… │
│ (BatchNormalizatio… │ None, 128)        │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_28 (Conv2D)  │ (None, None,      │      8,192 │ block1_conv2_act… │
│                     │ None, 128)        │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block2_pool         │ (None, None,      │          0 │ block2_sepconv2_… │
│ (MaxPooling2D)      │ None, 128)        │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, None,      │        512 │ conv2d_28[0][0]   │
│ (BatchNormalizatio… │ None, 128)        │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ add_85 (Add)        │ (None, None,      │          0 │ block2_pool[0][0… │
│                     │ None, 128)        │            │ batch_normalizat… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ block3_sepconv1_act │ (None, None,      │          0 │ add_85[0][0]    

 Total params: 20,861,480 (79.58 MB)

 Trainable params: 20,806,952 (79.37 MB)

 Non-trainable params: 54,528 (213.00 KB)

In [225]:
model = define_model(vocab_size, max_length)
model.summary()

Model: "functional_1"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_11      │ (None, 34)        │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ input_layer_10      │ (None, 2048)      │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding_1         │ (None, 34, 256)   │    982,016 │ input_layer_11[0… │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout_2 (Dropout) │ (None, 2048)      │          0 │ input_layer_10[0… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout_3 (Dropout) │ (None, 34, 256)   │          0 │ embedding_1[0][0] │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ not_equal_1         │ (None, 34)        │          0 │ input_layer_11[0… │
│ (NotEqual)          │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_3 (Dense)     │ (None, 256)       │    524,544 │ dropout_2[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ lstm_1 (LSTM)       │ (None, 256)       │    525,312 │ dropout_3[0][0],  │
│                     │                   │            │ not_equal_1[0][0] │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ add_97 (Add)        │ (None, 256)       │          0 │ dense_3[0][0],    │
│                     │                   │            │ lstm_1[0][0]      │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_4 (Dense)     │ (None, 256)       │     65,792 │ add_97[0][0]      │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_5 (Dense)     │ (None, 3836)      │    985,852 │ dense_4[0][0]     │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 3,083,516 (11.76 MB)

 Trainable params: 3,083,516 (11.76 MB)

 Non-trainable params: 0 (0.00 B)

In [230]:
epochs = 20
steps_per_epoch = 5
# os.mkdir("models")
for i in range(epochs):
    dataset = data_generator(train_descriptions, train_features, tokenizer, max_length, vocab_size)
    model.fit(dataset, epochs=10, steps_per_epoch=steps_per_epoch, verbose=1)
    model.save("models/model_" + str(i) + ".h5")

Epoch 1/10


ValueError: Missing data for input "input_layer_10". You passed a data dictionary with keys ['input_1', 'input_2']. Expected the following keys: ['input_layer_10', 'input_layer_11']